# CHAPTER 3 Discovering Groups

## Supervised versus Unsupervised Learning

## Word Vector

### Pigeonholing the Bloggers

In [1]:
import feedparser
import re

In [13]:
def getwordcount(url):
    # parse the feed
    d = feedparser.parse(url)
    wc = {}
    
    # loop over all entries
    for e in d.entries:
        if 'summary' in e:
            summary = e.summary
        else:
            summary = e.description
            
        # Extract a list of words
        words = getwords(e.title + ' ' + summary)
        for word in words:
            wc.setdefault(word, 0)
            wc[word] += 1
    return getattr(d.feed, 'title', 'Unknown title'), wc

In [17]:
def getwords(html):
    # remove all the html tags
    txt = re.compile(r'<[^>]+>').sub('', html)
    # split words by all non-alpha characters
    words = re.compile(r'[^A-Z^a-z]+').split(txt)
    # convert to lowcase
    return [word.lower() for word in words if word != '']

In [18]:
apcount = {}
wordcount = {}
for feedurl in file('feedlist.txt'):
    title, wc = getwordcount(feedurl)
    wordcount[title] = wc
    for word, count in wc.items():
        apcount.setdefault(word, 0)
        if count > 0:
            apcount[word] += 1

{'updated': u'2015-08-07T14:45:02Z', 'updated_parsed': time.struct_time(tm_year=2015, tm_mon=8, tm_mday=7, tm_hour=14, tm_min=45, tm_sec=2, tm_wday=4, tm_yday=219, tm_isdst=0), 'links': [{'href': u'http://guykawasaki.com/test-drive-mercedes-amg-gts/', 'type': u'text/html', 'rel': u'alternate'}], 'title': u'Test drive: Mercedes AMG GTS', 'author': u'Guy Kawasaki', 'summary_detail': {'base': u'http://guykawasaki.com/feed/rdf/', 'type': u'text/html', 'value': u'<p>My friends at Mercedes recently loaned me a Mercedes AMG to test drive, and I&#8217;d like to share my favorite pictures and thoughts\xa0with you. I hate to admit this, but I&#8217;m not sure I&#8217;m man enough for this car. It is a fantastic 503-horsepower engine (built by Sven Seyfried) with two seats strapped to the [&#8230;]</p>\n<p>The post <a href="http://guykawasaki.com/test-drive-mercedes-amg-gts/" rel="nofollow">Test drive: Mercedes AMG GTS</a> appeared first on <a href="http://guykawasaki.com" rel="nofollow">Guy Kawa

In [19]:
wordlist = []
for w, bc in apcount.items():
    frac = float(bc)/len(feedlist)
    if frac > 0.1 and frac < 0.5:
        wordlist.append(w)

In [21]:
out = file('blogdata.txt', 'w')
out.write('Blog')
for word in wordlist:
    out.write('\t%s' %word)
out.write('\n')

for blog, wc in wordcount.items():
    out.write(blog)
    for word in wordlist:
        if word in wc:
            out.write('\t%d' %wc[word])
        else:
            out.write('\t0')
    out.write('\n')

### Hierarchical Clustering

In [1]:
def readfile(filename):
    lines = [line for line in file(filename)]
    
    # first line the column title
    colnames = lines[0].strip().split('\t')[1: ]
    rownames = []
    data = []
    
    for line in lines[1: ]:
        p = line.strip().split('\t')
        # First column in each row is the row name
        rownames.append(p[0])
        data.append([float(x) for x in p[1: ]])
    return rownames, colnames, data

In [26]:
from math import sqrt

def pearson(v1, v2):
    # simple sum
    sum1 = sum(v1)
    sum2 = sum(v2)
    
    # sum of the squares
    sum1sq = sum([pow(v, 2) for v in v1])
    sum2sq = sum([pow(v, 2) for v in v2])
    
    # sum of the product
    psum = sum([v1[i]*v2[i] for i in range(len(v1))])
    
    # calculate r
    num = psum - (sum1*sum2/len(v1))
    den = sqrt((sum1sq - pow(sum1, 2)/len(v1)) * (sum2sq - pow(sum2, 2)/len(v2)))
    
    if den == 0:
        return 0
    return 1.0 - num/den    

In [11]:
class bicluster:
    def __init__(self, vec, left = None, right = None, distance = 0, id = None):
        self.left = left
        self.right = right
        self.vec = vec
        self.id = id
        self.distance = distance

In [27]:
def hcluster(rows, distance = pearson):
    distances = {}
    currentclustid = -1
    
    # clusters are initially just the rows
    clust = [bicluster(rows[i], id = 1) for i in range(len(rows))]
    
    while len(clust) > 1:
        lowestpair = (0, 1)
        closest = distance(clust[0].vec, clust[1].vec)
        
        ## Loop through every pair looking for the smallest distance
        for i in range(len(clust)):
            for j in range(len(clust)):
                # distance is the cache of distance calculation
                if (clust[i].id, clust[j].id) not in distances:
                    distances[(clust[i].id, clust[j].id)] = distance(clust[i].vec, clust[j].vec)
                
                d = distance(clust[i].vec, clust[j].vec)
                
                if d < closest:
                    closest = d
                    lowestpair = (i, j)
        # calculate the average of two clusters
        mergevec = [
            (clust[lowestpair[0]].vec[i] + clust[lowestpair[1]].vec[i])/2.0 for i in range(len(clust[0].vec))
        ]
        
        # create the new cluster
        newcluster  = bicluster(mergevec, left = clust[lowestpair[0]].vec, right= clust[lowestpair[1]].vec,
                               distance = closest, id = currentclustid)
        
        # cluster ids that weren't in the original set are nagtive
        currentclustid = -1
        del clust[lowestpair[0]]
        del clust[lowestpair[1]]
        clust.append(newcluster)

    return clust[0]        

In [28]:
blognames, words, data = readfile('blogdata.txt')

In [37]:
clust = hcluster(data)

In [39]:
def printclust(clust, labels = None, n = 0):
    # ident to make a hierarchy layout
    for i in range(n): print ' ',
    if clust.id < 0:
        # negative id means that this is branch
        print '-'
    else:
        #  positive id means this is an endpoint
        if labels == None:
            print clust.id
        else:
            print labels[clust.id]
    # Now print the left and right branches
    if clust.left != None:
        print printclust(clust.left, labels = labels, n = n + 1)
    if clust.right != None:
        print printclust(clust.right, labels = labels, n = n + 1)

In [42]:
printclust(clust, labels=blognames)

-
 

AttributeError: 'list' object has no attribute 'id'

In [34]:
# Now print the left and right branches
if clust.left != None:
    print printclust(clust.left, labels = labels, n = n + 1)
if clust.right != None:
    print printclust(clust.right, labels = labels, n = n + 1)

NameError: name 'labels' is not defined

### Drawing the Dendrogram

In [43]:
from PIL import Image, ImageDraw

ImportError: No module named PIL

In [44]:
def getheight(clust):
    ## Is this an endpoint? The the height is just -1
    if clust.left == None and clust.right == None:
        return 1
    
    # otherwise the height is the same height of each branch
    return getheight(clust, left) + getheight(clust, right)

In [45]:
def getdepth(clust):
    # The distance of the endpoint is 0
    if clust.left == None and clust.right == None:
        return 0
    
    # The distance of the branch is the greater if its two sides
    # Plus its own distance
    return max(getdepth(clust.left), getdepth(clust.right)) + clust.distance

In [46]:
def drawdendrogram(clust, labels, jpeg = 'clusters.jpg'):
    # height and width
    h = getheight(clust) * 20
    w = 120
    depth = getdepth(clust)
    
    # width is fixed, so scale distance accordingly
    scaling = float(w - 150)/depth
    
    # Create a new image with a white backgroud
    img = Image.new('RGB', (w, h), (255, 255, 255))
    draw = ImageDraw.Draw(img)
    
    draw.line((0, h/2, 10, h/2), fill = (255, 0, 0))
    
    # draw the first node
    drawnode(draw, clust, 10, (h/2), scaling, labels)
    img.save(jpeg, 'JPEG')

In [47]:
def drawnode(draw,clust,x,y,scaling,labels):
  if clust.id<0:
    h1=getheight(clust.left)*20
    h2=getheight(clust.right)*20
    top=y-(h1+h2)/2
    bottom=y+(h1+h2)/2
    # Line length
    ll=clust.distance*scaling
    # Vertical line from this cluster to children    
    draw.line((x,top+h1/2,x,bottom-h2/2),fill=(255,0,0))    
    
    # Horizontal line to left item
    draw.line((x,top+h1/2,x+ll,top+h1/2),fill=(255,0,0))    

    # Horizontal line to right item
    draw.line((x,bottom-h2/2,x+ll,bottom-h2/2),fill=(255,0,0))        

    # Call the function to draw the left and right nodes    
    drawnode(draw,clust.left,x+ll,top+h1/2,scaling,labels)
    drawnode(draw,clust.right,x+ll,bottom-h2/2,scaling,labels)
  else:   
    # If this is an endpoint, draw the item label
    draw.text((x+5,y-7),labels[clust.id],(0,0,0))

### Column Clusting

In [48]:
def rotatematrix(data):
    newdata = []
    for i in range(len(data[0])):
        newrow = [data[j][i] for j in range(len(data))]
        newdata.append(newrow)
    return newdata

## K-Means Clustering

In [50]:
import random

In [51]:
def kcluster(rows, distance = pearson, k = 4):
    #determina the minimum and maximum value for each points
    ranges = [(min([rows[i] for row in rows]), max([rows[i] for row in rows])) for i in range(len(rows[0]))]
    
    # create k randomly placed centroids
    clusters = [[random.random() * (ranges[i][1] - ranges[i][0]) + ranges[i][0] 
                 for i in range(len(rows[0]))] for j in range(k)]
    
    lastmatches = None
    for t in range(100):
        print 'Iteration %d' %i
        bestmatches = [[] for i in range(k)]
        
        # Find which centroid is the cloest for each row
        for j in range(len(rows)):
            row = rows[j]
            bestmatch = 0
            
            for i in range(k):
                d = distance(clusters[i], row)
                if d < distance(clusters[bestmatch], row):
                    bestmatch = i
            bestmatches[bestmatch].append(j)
 
        # If the result is the same as last time, this is complete
        if bestmatches == lastmatches:
            break
        lastmatches == bestmatches
        
        # Move to centroids to the average of their members
        for i in range(k):
            avgs = [0.0] * len(rows[0])
            if len(bestmatches[i]) > 0:
                for rowid in bestmatches[i]:
                    for m in range(len(rows(rowid))):
                        avgs[m] += rows[rowid][m]
                for j in range(len(avgs)):
                    avgs[i] /= len(bestmatches[j])
                clusters[i] = avgs
                
    return bestmatches

## Clusers of Preferences

### Getting and Preparing the Data

### Beautiful Soup

### Scraping the Zebo Results

In [53]:
from bs4 import BeautifulSoup
import urllib2
import re

chare = re.compile(r'[!-\.&]')
itemowners = {}

# words to remove
words = ['a', 'new', 'some', 'my', 'own', 'the', 'many', 'other', 'another']

currentuser = 0

for i in range(1,51):
  # URL for the want search page
  c=urllib2.urlopen(
  'http://member.zebo.com/Main?event_key=USERSEARCH&wiowiw=wiw&keyword=car&page=%d'
  % (i))
  soup=BeautifulSoup(c.read())
  for td in soup('td'):
    # Find table cells of bgverdanasmall class
    if ('class' in dict(td.attrs) and td['class']=='bgverdanasmall'):
      items=[re.sub(chare,'',str(a.contents[0]).lower()).strip() for a in td('a')]
      for item in items:
        # Remove extra words
        txt=' '.join([t for t in item.split(' ') if t not in dropwords])
        if len(txt)<2: continue
        itemowners.setdefault(txt,{})
        itemowners[txt][currentuser]=1
      currentuser+=1

URLError: <urlopen error [Errno 110] Connection timed out>

In [ ]:
out=file('zebo.txt','w')
out.write('Item')
for user in range(0,currentuser): out.write('\tU%d' % user)
out.write('\n')
for item,owners in itemowners.items():
  if len(owners)>10:
    out.write(item)
    for user in range(0,currentuser):
      if user in owners: out.write('\t1')
      else: out.write('\t0')
    out.write('\n')

In [54]:
def tanamto(v1, v2):
    c1, c2, shr = 0, 0, 0
    
    for i in range(len(v1)):
        if v1[i] != 0:
            c1 += 1
        if v2[i] != 0:
            c2 += 1
        if v1[i] != 0 and v2[i] != 0:
            shr += 1
    return 1.0 - (float(shr)/(c1 + c2 - shr))

### Clustering Result

In [55]:
def scaledown(data,distance=pearson,rate=0.01):
  n=len(data)

  # The real distances between every pair of items
  realdist=[[distance(data[i],data[j]) for j in range(n)] 
             for i in range(0,n)]

  # Randomly initialize the starting points of the locations in 2D
  loc=[[random.random(),random.random()] for i in range(n)]
  fakedist=[[0.0 for j in range(n)] for i in range(n)]
  
  lasterror=None
  for m in range(0,1000):
    # Find projected distances
    for i in range(n):
      for j in range(n):
        fakedist[i][j]=sqrt(sum([pow(loc[i][x]-loc[j][x],2) 
                                 for x in range(len(loc[i]))]))
  
    # Move points
    grad=[[0.0,0.0] for i in range(n)]
    
    totalerror=0
    for k in range(n):
      for j in range(n):
        if j==k: continue
        # The error is percent difference between the distances
        errorterm=(fakedist[j][k]-realdist[j][k])/realdist[j][k]
        
        # Each point needs to be moved away from or towards the other
        # point in proportion to how much error it has
        grad[k][0]+=((loc[k][0]-loc[j][0])/fakedist[j][k])*errorterm
        grad[k][1]+=((loc[k][1]-loc[j][1])/fakedist[j][k])*errorterm

        # Keep track of the total error
        totalerror+=abs(errorterm)
    print totalerror

    # If the answer got worse by moving the points, we are done
    if lasterror and lasterror<totalerror: break
    lasterror=totalerror
    
    # Move each of the points by the learning rate times the gradient
    for k in range(n):
      loc[k][0]-=rate*grad[k][0]
      loc[k][1]-=rate*grad[k][1]

  return loc

In [56]:
def draw2d(data,labels,jpeg='mds2d.jpg'):
  img=Image.new('RGB',(2000,2000),(255,255,255))
  draw=ImageDraw.Draw(img)
  for i in range(len(data)):
    x=(data[i][0]+0.5)*1000
    y=(data[i][1]+0.5)*1000
    draw.text((x,y),labels[i],(0,0,0))
  img.save(jpeg,'JPEG')  

### Other Things to  Cluster